In [ ]:
import os

from dotenv import load_dotenv

load_dotenv()
token = os.getenv("HUGGINGFACE_TOKEN")

from huggingface_hub import login

login(token=os.environ["HUGGINGFACE_TOKEN"])

# # Run isort on all folders
# isort .
# # Run black on all folders
# black .
# # Run flake8 on all folders
# flake8 .

# # Run pylint on all folders
# pylint .

/home/boom/.pyenv/versions/rag/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
help(load_dataset)

Help on function load_dataset in module datasets.load:

load_dataset(path: str, name: Optional[str] = None, data_dir: Optional[str] = None, data_files: Union[str, collections.abc.Sequence[str], collections.abc.Mapping[str, Union[str, collections.abc.Sequence[str]]], NoneType] = None, split: Union[str, datasets.splits.Split, NoneType] = None, cache_dir: Optional[str] = None, features: Optional[datasets.features.features.Features] = None, download_config: Optional[datasets.download.download_config.DownloadConfig] = None, download_mode: Union[datasets.download.download_manager.DownloadMode, str, NoneType] = None, verification_mode: Union[datasets.utils.info_utils.VerificationMode, str, NoneType] = None, keep_in_memory: Optional[bool] = None, save_infos: bool = False, revision: Union[str, datasets.utils.version.Version, NoneType] = None, token: Union[bool, str, NoneType] = None, streaming: bool = False, num_proc: Optional[int] = None, storage_options: Optional[dict] = None, trust_remote_co

In [5]:
from datasets import load_dataset

dataset = load_dataset(
    "gaia-benchmark/GAIA",
    name="2023_level1",
    split="validation",
    trust_remote_code=True,
    cache_dir="ragdata",
)

2023 1


Generating test split: 93 examples [00:00, 10442.25 examples/s]
Generating validation split: 53 examples [00:00, 7329.56 examples/s]


In [8]:
os.listdir(
    r"ragdata/gaia-benchmark___gaia/2023_level1/0.0.1/ec492fe4320ee795b1aed6bb46229c5f693226b0f1316347501c24b4baeee005"
)

['dataset_info.json', 'gaia-validation.arrow', 'gaia-test.arrow']

In [ ]:
from datasets import load_dataset
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.schema import Document
from langchain.vectorstores import Chroma

# Load the GAIA validation dataset
dataset = load_dataset(
    "gaia-benchmark/GAIA",
    name="2023_level1",
    split="validation",
    trust_remote_code=True,
    cache_dir="ragdata",
)
# Prepare the embeddings model
embeddings = HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")

# Extract questions and their answers
documents = []
for entry in dataset:
    question = entry["Question"]
    answer = entry["Final answer"]

    # Create a document with both the question and the answer as metadata
    metadata = {
        "task_id": entry["task_id"],
        "steps": entry["Annotator Metadata"]["Steps"],
        "tools": entry["Annotator Metadata"]["Tools"],
        "answer": answer,
    }

    # Add the question to the list of documents
    documents.append(Document(page_content=question, metadata=metadata))

# Insert the documents into Chroma
vectorstore = Chroma.from_documents(
    documents=documents,
    embedding=embeddings,
    collection_name="gaia_validation",
    persist_directory="./chroma_store",
)

# Persist the data for future use
vectorstore.persist()

/tmp/ipykernel_15347/1929323449.py:43: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  vectorstore.persist()


In [13]:
from datasets import load_dataset

# Load the GAIA validation dataset
dataset = load_dataset("gaia-benchmark/GAIA", name="2023_level1", split="validation")

# Initialize a set to store unique tools
unique_tools = set()

# Iterate over each entry in the dataset
for entry in dataset:
    # Access the tools used (they are stored in the 'Tools' field of 'Annotator Metadata')
    tools = entry["Annotator Metadata"]["Tools"]

    # Split the tools into a list (since they are stored as a string, we split by line breaks)
    tools_list = tools.split("\n")

    # Add each tool to the set (set automatically ensures uniqueness)
    for tool in tools_list:
        unique_tools.add(tool.strip())  # Remove any extra spaces or newlines

# Convert the set of unique tools to a dictionary under the key 'tools'
tools_dict = {"tools": list(unique_tools)}

# Print the unique tools to get a sense of what was used
print(tools_dict)

{'tools': ['1. A calculator', '3. Video recognition tools', '1. A web browser.', '2. google search', '2. Web browser', '1. web browser', '2. calculator', '2. A speech-to-text tool', '3. Calculator', '1. Wikipedia', '3. Audio capability', '3. Color recognition', '1. Markdown', '2. Video processing software', '1. search engine', 'No tools required', '2. Video parsing', '1. A word reversal tool / script', '1. Image recognition tools', '2. Image recognition', '2. Calculator', '2. search engine', '2. Search engine', '1. Access to Excel files', '1. Web browser', '1. Calculator', '1. Search engine', '1. Text Editor', '1. PowerPoint viewer', '3. PDF access', '1. image recognition/OCR', '2. A search engine.', '3. Audio processing software', '1. Excel', '3. PDF viewer', '3. A calculator.', "1. Rubik's cube model", '1. Word document access', 'None', '1. A file interface', '3. Access to academic journal websites', '2. Color recognition', '3. Calculator (or ability to count)', '1. Python', '2. A sp